# Analyzing link budget for a medical body area network

You are working as an engineer in a large regional hospital. Some physicians expressed their interest in getting a new telemedicine system to monitor patients over a week or so. The device will be worn on a body and will both monitor, e.g., blood pressure and act on the body, e.g., [electrical muscle stimulation](https://en.wikipedia.org/wiki/Electrical_muscle_stimulation). The system supports the incorporation of many sensors worn on many patients, which should have enough bandwidth for reliable operation, and you want to analyze whether the system is feasible in your work environment.

[medical body area network (MBAN)](https://en.wikipedia.org/wiki/Body_area_network)
: a wireless network of medical wearable computing devices

The system creates an MBAN.

Technical details:
- Based on [Medical Device Radiocommunications Service](https://en.wikipedia.org/wiki/Medical_Device_Radiocommunications_Service) and uses 2360-2400 MHz band.
- data rate: 125 kb/s, bandwidth is limited to 2 MHz
  - similar to [Bluetooth 6.0 Low Energy PHY spec](https://www.bluetooth.com/wp-content/uploads/Files/Specification/HTML/Core-60/out/en/low-energy-controller/physical-layer-specification.html) (Excerpt: *125 kb/s ±1 ppm for the LE Coded PHY when using S=8 coding, The LE system uses 40 RF channels with center frequencies at a 2 MHz spacing from 2402 MHz to 2480 MHz.*)
- the sensors are configured to send a packet every 100 ms.
- packet size: 32 bytes
  - contains complete physiological data
- maximum $P_\mathrm{tx} \approx 1 \mathrm{mW} = -30 \mathrm{dBW}$
  - similar to sensors based on [Bluetooth 6.0 Low Energy power class 3](https://www.bluetooth.com/wp-content/uploads/Files/Specification/HTML/Core-60/out/en/low-energy-controller/physical-layer-specification.html#UUID-bbd493bf-d91a-50c6-6efc-1ab9b7b5ebd0_table-idm13359020065088) (Excerpt: *1 mW (0 dBm) ≥ Pmax ≥ 0.01 mW (-20 dBm)*)
- sensor has a patch antenna $G_\mathrm{tx}$ about 2 dB
- a central receiver antenna has $G_\mathrm{rx}$ about 3 dB
  - placed in the middle of the hospital floor
- the hospital floor spans an area of 100m x 30m
  - has many rooms

Questions about requirements:
- Does the system have enough link budget for a reliable reception at the central receiver?
  - First assume an LOS transmission in a hospital room. 
  - Then analyze the actual case
- Is the data rate sufficient?
- The device can house two rechargeable AA batteries. Is this sufficient to power one device for over a week?

*If any requirement is not sufficient: do you have any suggestions for improvement?*

  <!--
  - uses QPSK
- BER < $10^{-10}$
  - based on [select BAN applications](https://pmc.ncbi.nlm.nih.gov/articles/PMC9105253/table/sensors-22-03539-t003/)
- Is the modulation scheme appropriate for the given BER?
-->

<!-- how much can we reduce the P_tx ? -->

## Preparation

- Read: <https://pysdr.org/content/link_budgets.html>
- Quiz: {ref}`sec:linkbudgetquiz` 

## In-class activities

- [mini lecture](link-budget.md)

## Solution

Constants

In [1]:
P_TX_DB = -30  # dB
G_TX_DB = 2
G_RX_DB = 3
L_MISC_DB = 6
FLOOR_WIDTH = 100  # m
FLOOR_HEIGHT = 30
F = 2400e6  # Hz, Worst case
# We want to analyze the worst case.
# Worst case frequency is 2400 MHz because attenuation at higher frequencies is higher.

# For the thermal noise
BANDWIDTH = 2e6  # Hz
TEMPERATURE = 290  # K

# ITU indoor model
N_OFFICE_2GHZ = 30  # Office area 1.8-2 GHz
P_F_SAME_FLOOR = 0  # Same floor

DATA_RATE = 125e3  # bits
PACKET_SIZE = 32 * 8  # bits

Furthest distance from the receiver based on the diagonal of the floor

In [2]:
from sympy import sqrt

(distance := sqrt(FLOOR_WIDTH**2 + FLOOR_HEIGHT**2) / 2)

5*sqrt(109)

Define link budget equations in dB:

### Free-space model

In [3]:
from sympy import Eq, log, symbols

l_fs, d, f = symbols(r"l_\mathrm{fs} d, f")
(l_fs_eq := Eq(l_fs, 20 * log(d, 10) + 20 * log(f, 10) - 147.55))

Eq(l_\mathrm{fs}, 20*log(d)/log(10) + 20*log(f)/log(10) - 147.55)

### ITU indoor model

In [4]:
l_itu, n, p_f = symbols(r"l_\mathrm{itu-indoor} n p_\mathrm{f}")
(l_itu_eq := Eq(l_itu, 20 * log(f, 10) + n * log(d, 10) + p_f - 28))

Eq(l_\mathrm{itu-indoor}, n*log(d)/log(10) + p_\mathrm{f} + 20*log(f)/log(10) - 28)

### $p_\mathrm{rx}$

In [5]:
snr, p_tx, g_tx, l_p, g_rx, l_misc, p_rx, l_thermal = symbols(
    r"""
    \mathrm{snr}
    p_\mathrm{tx}
    g_\mathrm{tx}
    l_\mathrm{p} 
    g_\mathrm{rx}
    l_\mathrm{misc}
    p_\mathrm{rx}
    l_\mathrm{thermal}
    """
)
(p_rx_eq := Eq(p_rx, p_tx + g_tx - l_p + g_rx - l_misc))

Eq(p_\mathrm{rx}, g_\mathrm{rx} + g_\mathrm{tx} - l_\mathrm{misc} - l_\mathrm{p} + p_\mathrm{tx})

### Thermal noise

In [6]:
from math import log10

from scipy.constants import Boltzmann

B = 10 * log10(BANDWIDTH)  # dBHz
t = 10 * log10(TEMPERATURE)  # dBK
k = 10 * log10(Boltzmann)  # dBW/K/Hz
(l_thermal_db := B + t + k)

-140.9648872375883

### SNR

In [7]:
(snr_eq := Eq(snr, p_rx - l_thermal))

Eq(\mathrm{snr}, -l_\mathrm{thermal} + p_\mathrm{rx})

### Substitution and numeric evaluation free-space model

Substitute and use $l_\mathrm{fs}$ as $l_\mathrm{p}$.

In [8]:
subs = {
    p_tx: P_TX_DB,
    g_tx: G_TX_DB,
    d: distance,
    f: F,
    g_rx: G_RX_DB,
    l_misc: L_MISC_DB,
    l_thermal: l_thermal_db,
    p_rx: p_rx_eq.rhs,
}
subs_fs = subs.copy()
subs_fs.update(
    {
        l_p: l_fs_eq.rhs,
    }
)

$p_\mathrm{rx}$

In [9]:
(p_rx_evald := p_rx_eq.rhs.evalf(subs=subs_fs))

-105.407889900359

$p_\mathrm{rx}$:

SNR

In [10]:
(snr_evald := snr_eq.rhs.evalf(subs=subs_fs))

35.5569973372296

In [11]:
l_fs_eq.rhs.evalf(subs=subs_fs)

74.4078899003587

In [12]:
import pandas as pd


def display_table(subs):
    data = [
        ["p_tx", P_TX_DB],
        ["g_tx", G_TX_DB],
        ["l_p", -int(l_p.evalf(subs=subs))],
        ["g_rx", G_RX_DB],
        ["l_misc", -L_MISC_DB],
        ["p_rx", int(p_rx_evald)],
        ["l_thermal", int(-l_thermal_db)],
        ["snr", int(snr_eq.rhs.evalf(subs=subs))],
    ]
    # TODO convert them to Latex symbols
    # using `p_tx` and then wrapping with $ works in Jupyter
    # but not in HTML output

    df = pd.DataFrame(data)
    df.columns = ["Parameter", "Value"]

    return df


display_table(subs_fs)

Parameter  Value
0       p_tx    -30
1       g_tx      2
2        l_p    -74
3       g_rx      3
4     l_misc     -6
5       p_rx   -105
6  l_thermal    140
7        snr     35

### Substitution and numeric evaluation ITU model

In [13]:
subs_itu = subs.copy()
subs_itu.update(
    {
        l_p: l_itu_eq.rhs,
        n: N_OFFICE_2GHZ,
        p_f: P_F_SAME_FLOOR,
    }
)
display_table(subs_itu)

Parameter  Value
0       p_tx    -30
1       g_tx      2
2        l_p   -211
3       g_rx      3
4     l_misc     -6
5       p_rx   -105
6  l_thermal    140
7        snr   -101

### Data rate sufficient?

In [14]:
(transmitted_bits_per_second := PACKET_SIZE * 10)

2560

In [15]:
print("Yes" if DATA_RATE >= transmitted_bits_per_second else "No")

Yes


### Battery consumption analysis

In [16]:
(duty_cycle := transmitted_bits_per_second/ DATA_RATE )

0.02048

In [17]:
p_tx_linear = 10 ** (P_TX_DB / 10)  # W
energy_for_one_week = p_tx_linear * duty_cycle * 60 * 60 * 24 * 7
print(f"Energy needed for one week: {energy_for_one_week}")

Energy needed for one week: 12.386303999999999


In [18]:
RECHARGABLE_AA_BATTERY_ENERGY = 1.2 * 2.5 * 60 * 60  # 1.2 V * 2500 mAh
print("2 rechargable AA batteries' energy: ", 2 * RECHARGABLE_AA_BATTERY_ENERGY)

2 rechargable AA batteries' energy:  21600.0


In [19]:
print("Two AA sufficient?")
print("Yes" if 2 * RECHARGABLE_AA_BATTERY_ENERGY > energy_for_one_week else "No")

Two AA sufficient?
Yes


### Is the modulation scheme appropriate?

In [20]:
# For 10^-10 we need 14 dB @QPSK
EB_PER_N0_DB = 14  # dB
R_B = 125e3  # bit
eb_per_n0 = 10 ** (EB_PER_N0_DB / 10)


n_0 = Boltzmann * TEMPERATURE
e_b = eb_per_n0 * n_0
p_rx_ = e_b * R_B
p_rx_db_ = 10 * log(p_rx_, 10)
print(f"Minimum P_rx ~{int(p_rx_db_)} dB")
print()

Minimum P_rx ~-139 dB



In [21]:
print("Modulation scheme appropriate for free-space?")
print("Yes" if p_rx.evalf(subs=subs_fs) > p_rx_db_ else "No")

Modulation scheme appropriate for free-space?
Yes


In [22]:
print("Modulation scheme appropriate for ITU indoor?")
print("Yes" if p_rx.evalf(subs=subs_itu) > p_rx_db_ else "No")

Modulation scheme appropriate for ITU indoor?
No


### Conclusions

The device does not have enough link margin.
- LOS transmission feasible, but obstructed (non-LOS) transmission not possible
- Every room should have a receiver

One week runtime is not possible. 
- The batteries could be changed more often
- The measurement frequency could be reduced.